In [8]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [9]:
import tensorflow as tf
from tensorflow.keras.layers import Dense, Conv2D, Reshape
from polymap import Polymap
from aesthetic_loss import aesthetic_loss

In [46]:
from math import pi
squares = [chr(i) for i in range(0x1F7E5, 0x1F7EC)]
tfsquares = tf.constant(squares)
print(squares)
colors = tf.constant([10, 219, 38, 48, 80,  282, 20] * tf.constant(pi/180.0), dtype=tf.float32)
color_vectors = tf.transpose(
    tf.stack([
    tf.math.cos(colors),
    tf.math.sin(colors)]
    )
)

def vector_to_index(tensor):
    return tf.argmax((tf.einsum("ijk,lk->ijl", tensor, color_vectors)), axis=-1)

def index_to_string(tensor):
    # square_select = tf.math.argmax(tensor, 2)

    tfstring = tf.strings.join(
        tf.map_fn(
            lambda v:
            tf.strings.join(
                tf.gather(tfsquares, tf.cast(v, tf.int64))), tensor, fn_output_signature=tf.string), "\n")

    return tfstring.numpy().decode()

['🟥', '🟦', '🟧', '🟨', '🟩', '🟪', '🟫']


In [10]:
batch_size = 16

In [51]:
# class PatchGen(tf.keras.Model):

#     def __init__(self, batch_size):
#         super(PatchGen, self).__init__()
#         self.pm = Polymap(8, 3)(input)
#         self.d1 = Dense(64)
#         self.rs = Reshape([8,8,1])
#         self.dc1 = Conv2D(3,(1,1))

#     def call(self, inputs):
#         x = self.block_1(inputs)
#         x = self.block_2(x)
#         x = self.global_pool(x)
#         return self.classifier(x)

input = tf.random.normal(shape=[batch_size,2])
pm = Polymap(8, 3)
d1 = Dense(64, activation="relu")
d2 = Dense(64, activation="relu")
rs = Reshape([8,8,1])
dc1 = Conv2D(2,(1,1))

def gen():
    input = tf.random.normal(shape=[batch_size,2])
    x = pm(input)
    x = d1(x)
    x = d2(x)
    x = rs(x)
    return dc1(x)
# gen()

In [52]:
optimizer = tf.keras.optimizers.Adam()
train_loss = tf.keras.metrics.Mean(name='train_loss')

In [53]:
@tf.function
def train_step():
    with tf.GradientTape() as tape:
        pics = gen()
        loss = aesthetic_loss(pics)
    tv = sum([pm.trainable_weights, d1.trainable_weights,
             dc1.trainable_weights], [])
    print(tv)
    gradients = tape.gradient(loss, tv)
    optimizer.apply_gradients(zip(gradients, tv))

    train_loss(loss)
    # train_accuracy(labels, predictions)

In [57]:
EPOCHS = 50

for epoch in range(EPOCHS):
    # Reset the metrics at the start of the next epoch
    train_loss.reset_states()
#   train_accuracy.reset_states()
#   test_loss.reset_states()
#   test_accuracy.reset_states()

#   for images, labels in train_ds:
    for i in range(50):
        train_step()

#   for test_images, test_labels in test_ds:
#     test_step(test_images, test_labels)

    print(
        f'Epoch {epoch + 1}, '
        f'Loss: {train_loss.result()}, '
        # f'Accuracy: {train_accuracy.result() * 100}, '
        # f'Test Loss: {test_loss.result()}, '
        # f'Test Accuracy: {test_accuracy.result() * 100}'
    )

    ps = gen()
    # print(ps[0])
    print(index_to_string(vector_to_index(ps[0])))

Epoch 1, Loss: 0.0004605448921211064, 
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
Epoch 2, Loss: 9.45829197007697e-06, 
🟥🟥🟥🟥🟥🟥🟥🟥
🟥🟥🟥🟥🟥🟥🟥🟥
🟥🟥🟥🟥🟥🟥🟥🟥
🟥🟥🟥🟥🟥🟥🟥🟥
🟥🟥🟥🟥🟥🟥🟥🟥
🟥🟥🟥🟥🟥🟥🟥🟥
🟥🟥🟥🟥🟥🟥🟥🟥
🟥🟥🟥🟥🟥🟥🟥🟥
Epoch 3, Loss: 8.17671389086172e-05, 
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
Epoch 4, Loss: 0.0001505890249973163, 
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
Epoch 5, Loss: 0.00018983485642820597, 
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
Epoch 6, Loss: 0.00012902110756840557, 
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
Epoch 7, Loss: 1.342521863989532e-05, 
🟨🟨🟨🟨🟨🟨🟨🟨
🟨🟨🟨🟨🟨🟨🟨🟨
🟨🟨🟨🟨🟨🟨🟨🟨
🟨🟨🟨🟨🟨🟨🟨🟨
🟨🟨🟨🟨🟨🟨🟨🟨
🟨🟨🟨🟨🟨🟨🟨🟨
🟨🟨🟨🟨🟨🟨🟨🟨
🟨🟨🟨🟨🟨🟨🟨🟨
Epoch 8, Loss: 0.00034237385261803865, 
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
🟩🟩🟩🟩🟩🟩🟩🟩
Epoch 9, Loss: 8.251221879618242e-05, 
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
🟦🟦🟦🟦🟦🟦🟦🟦
